# Instalacja pakietów

In [1]:
!pip install transformers datasets torch sentencepiece

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 34.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 462.8/462.8 KB 27.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 52.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 15.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 55.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.0/132.0 KB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.0/213.0 KB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 KB 10.4 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


# Załadowanie datasetu

In [2]:
from datasets import load_dataset

In [3]:
dataset = load_dataset("sms_spam")

Generating train split:   0%|          | 0/5574 [00:00<?, ? examples/s]

Dataset sms_spam downloaded and prepared to /root/.cache/huggingface/datasets/sms_spam/plain_text/1.0.0/53f051d3b5f62d99d61792c91acefe4f1577ad3e4c216fb0ad39e30b9f20019c. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
dataset['train'][0]

{'sms': 'Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...\n',
 'label': 0}

# Przygotowanie datasetu

In [5]:
parsed_dataset = []

for row in dataset['train']:
  text = row['sms'].replace("\n", "")
  new_row = {}
  new_row['sms'] = text
  if row['label'] == 0:
    new_row['label'] = "False"
  else:
    new_row['label'] = "True"
  parsed_dataset.append(new_row)

parsed_dataset[0]

{'sms': 'Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...',
 'label': 'False'}

# Tokenizer FLAN-T5

In [6]:
from transformers import AutoTokenizer

In [7]:
tokenizer = AutoTokenizer.from_pretrained('google/flan-t5-large')

In [8]:
sms = parsed_dataset[0]['sms']
print('Original: ', sms)
print('Tokenized: ', tokenizer.tokenize(sms))
print('Token IDs: ', tokenizer.convert_tokens_to_ids(tokenizer.tokenize(sms)))

Original:  Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...
Tokenized:  ['▁Go', '▁until', '▁jur', 'ong', '▁point', ',', '▁crazy', '.', '.', '▁Available', '▁only', '▁in', '▁bug', 'is', '▁', 'n', '▁great', '▁world', '▁la', '▁', 'e', '▁buffet', '...', '▁Cine', '▁there', '▁got', '▁', 'a', 'more', '▁wa', 't', '...']
Token IDs:  [1263, 552, 10081, 2444, 500, 6, 6139, 5, 5, 8144, 163, 16, 8143, 159, 3, 29, 248, 296, 50, 3, 15, 15385, 233, 17270, 132, 530, 3, 9, 3706, 8036, 17, 233]


# Few shot learning

In [9]:
print(parsed_dataset[0]) #0
print(parsed_dataset[123]) #1
print(parsed_dataset[2000]) #0
print(parsed_dataset[3002]) #1

{'sms': 'Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...', 'label': 'False'}
{'sms': 'Todays Voda numbers ending 7548 are selected to receive a $350 award. If you have a match please call 08712300220 quoting claim code 4041 standard rates app', 'label': 'True'}
{'sms': "LMAO where's your fish memory when I need it?", 'label': 'False'}
{'sms': 'This message is free. Welcome to the new & improved Sex & Dogging club! To unsubscribe from this service reply STOP. msgs@150p 18+only', 'label': 'True'}


In [10]:
non_spam_1 = "The text message contains the following content: " + parsed_dataset[0]['sms'] + "\nIs it true that the content of a text message is spam: False\n\n"
spam_1 = "The text message contains the following content: " + parsed_dataset[123]['sms'] + "\nIs it true that the content of a text message is spam: True\n\n"
non_spam_2 = "The text message contains the following content: " + parsed_dataset[2000]['sms'] + "\nIs it true that the content of a text message is spam: False\n\n"
spam_2 = "The text message contains the following content: " + parsed_dataset[3002]['sms'] + "\nIs it true that the content of a text message is spam: True\n\n"

few_shot_prefix = non_spam_1 + spam_1 + non_spam_2 + spam_2 + "The text message contains the following content: "
print(few_shot_prefix)

The text message contains the following content: Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...
Is it true that the content of a text message is spam: False

The text message contains the following content: Todays Voda numbers ending 7548 are selected to receive a $350 award. If you have a match please call 08712300220 quoting claim code 4041 standard rates app
Is it true that the content of a text message is spam: True

The text message contains the following content: LMAO where's your fish memory when I need it?
Is it true that the content of a text message is spam: False

The text message contains the following content: This message is free. Welcome to the new & improved Sex & Dogging club! To unsubscribe from this service reply STOP. msgs@150p 18+only
Is it true that the content of a text message is spam: True

The text message contains the following content: 


# Load FLAN-T5 model

In [11]:
from transformers import AutoModelForSeq2SeqLM

In [12]:
model = AutoModelForSeq2SeqLM.from_pretrained('google/flan-t5-large')

model.cuda()

T5ForConditionalGeneration(
  (shared): Embedding(32128, 1024)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 1024)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=1024, out_features=1024, bias=False)
              (k): Linear(in_features=1024, out_features=1024, bias=False)
              (v): Linear(in_features=1024, out_features=1024, bias=False)
              (o): Linear(in_features=1024, out_features=1024, bias=False)
              (relative_attention_bias): Embedding(32, 16)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=1024, out_features=2816, bias=False)
              (wi_1): Linear(in_features=1024, out_features=2816, bias=False)
       

# Helper functions

In [13]:
import torch

In [14]:
def calculate_accuracy(preds, target):
  results_ok = 0.0
  results_false = 0.0

  for idx, pred in enumerate(preds):
    if pred == target[idx]:
      results_ok += 1.0
    else:
      results_false += 1.0

  return results_ok / (results_ok + results_false)

In [15]:
if torch.cuda.is_available():     
    device = torch.device("cuda")

    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))

else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

There are 1 GPU(s) available.
We will use the GPU: Tesla T4


# Predykcja

In [17]:
parsed_dataset = parsed_dataset[1:123] + parsed_dataset[124:2000] + parsed_dataset[2001:3002] + parsed_dataset[3003:]
predictions = []
expected = []

for row in parsed_dataset:
  input_text = few_shot_prefix + row['sms'] + "\nIs it true that the content of a text message is spam: "
  input_ids = tokenizer(input_text, return_tensors="pt").input_ids.to(device)

  generated_ids = model.generate(input_ids, do_sample=True, temperature=0.9, max_length=250)
  generated_text = tokenizer.decode(generated_ids[0], skip_special_tokens=True, clean_up_tokenization_spaces=True)
  
  predictions.append(generated_text)
  expected.append(row['label'])

acc = calculate_accuracy(predictions, expected)
print(acc)

0.1433704635285663


In [18]:
print("Sample prediction: {}, expected: {}".format(predictions[101], expected[101]))

Sample prediction: False, expected: False


# MCC Score

In [19]:
from sklearn.metrics import matthews_corrcoef

print('Calculating Matthews Corr. Coef. for each batch...')
matthews = matthews_corrcoef(expected, predictions)    
print('Total MCC: %.3f' % matthews)

Calculating Matthews Corr. Coef. for each batch...
Total MCC: 0.055


# Save model

In [20]:
from google.colab import drive

drive.mount('/content/gdrive/', force_remount=True)

output_dir = '/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model'
print("Saving model to %s" % output_dir)

model_to_save = model.module if hasattr(model, 'module') else model
model_to_save.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

Mounted at /content/gdrive/
Saving model to /content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model


('/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model/tokenizer_config.json',
 '/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model/special_tokens_map.json',
 '/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model/spiece.model',
 '/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model/added_tokens.json',
 '/content/gdrive/My Drive/UAM/Przetwarzanie-tekstu/Ver_4_FLAN-T5_Model/tokenizer.json')

# Bibliografia
- https://huggingface.co/docs/transformers/main/en/model_doc/flan-t5
- https://mccormickml.com/2019/07/22/BERT-fine-tuning/#a1-saving--loading-fine-tuned-model
- https://huggingface.co/docs/transformers/model_doc/t5#training